Making a Game of Texas Hold'em

1. run the first block
2. run the second block. the second block is where the game takes place

In [1]:
import random as rand

# creating the card class for the deck class to now be able to hold onto card suits and values
class Card:
  def __init__(self,suit,rank,value):
    self.suit = suit
    self.rank = rank
    self.value = value
  def __repr__(self): # tells you what the card actually is (needed help from the internet to do this)
      return f"{self.rank} of {self.suit}"

#creating deck class to have all the initial things needed to then have poker logic
class Deck:
  def __init__(self, number_of_decks): # hold all the ranks for cards
    self.number_of_decks = int(number_of_decks)
    self.table_cards = [] # shows all the cards on the table
    self.all_cards = [] # holds all cards not used right now. first holds all 52 cards, then goes down as the game goes on
    self.discards = [] # holds all the discarded cards. first holds 0, then increases as the game goes on
    suits = number_of_decks*["Hearts", "Diamonds", "Clubs", "Spades"]
    ranks = ["Two", "Three", "Four", "Five", "Six", "Seven", "Eight", "Nine", "Ten", "Jack", "Queen", "King", "Ace"]
    card_value = {"Two": 2, "Three": 3, "Four": 4, "Five": 5, "Six": 6, "Seven": 7, "Eight": 8, "Nine": 9, "Ten": 10, "Jack": 11, "Queen": 12, "King": 13, "Ace": 14}
    for suit in suits: # collects all the cards and puts them in the all_cards list
      for rank in ranks:
        value = card_value[rank]
        newcard = Card(suit,rank,value)
        self.all_cards.append(newcard)
  def shuffle(self): # shuffles cards
    rand.shuffle(self.all_cards)
  def deal(self): # deals the cards to the person's hand
    return [self.all_cards.pop(), self.all_cards.pop()]
  def deal_one(self): # deals one onto the table. if there are 5 cards on the table, no more are dealt
    if len(self.table_cards) < 5:
      self.table_cards.append(self.all_cards.pop())
    return self.table_cards

#creating a class to do all the logic for how poker works
class HandEvaluator:
  def __init__(self,hand_cards,table_cards):
    self.all_cards = hand_cards + table_cards # creates a list of all the cards on the table
    self.suits_total = {"Hearts": 0, "Diamonds": 0, "Clubs": 0, "Spades": 0}
    self.values_total =  {2: 0, 3: 0, 4: 0, 5: 0, 6: 0, 7: 0, 8: 0, 9: 0, 10: 0, 11: 0, 12: 0, 13: 0, 14: 0}
    for card in self.all_cards:
      self.suits_total[card.suit] += 1
      self.values_total[card.value] += 1

    # sorting through to create a list from least to greatest values
    n = len(self.all_cards)
    for i in range(n): # goes through every combination 1 by 1 (first 4 steps, then 3, then 2, then 1)
      for j in range(0, n-i-1): # says that if the first value is bigger than the second value, they switch spots
        if self.all_cards[j].value > self.all_cards[j + 1].value:
            self.all_cards[j], self.all_cards[j + 1] = self.all_cards[j + 1], self.all_cards[j]
    self.total_sorter = self.all_cards

  def flush(self): # checking to see if there is a flush (5 of the same suit)
    flush_suit = None # finding which suit brings the flush, if there is a flush
    for suit, count in self.suits_total.items():
        if count >= 5:
            flush_suit = suit
            break
    if flush_suit: # grab the highest value if there is a suit
        cards_of_suit = [card for card in self.all_cards if card.suit == flush_suit] # puts a list of all the cards in the same suit
        flush_values = [card.value for card in cards_of_suit] # takes the values of the cards
        self.best_five_flush = sorted(flush_values, reverse=True)[:5] # makes a list of those card values from lowest to greatest
        return True, self.best_five_flush[-1]
    for count in self.suits_total.values():
        if count >= 5:
            return True, self.best_five_flush[-1]
    return False, 0

  def straight(self): # checking to see if there is a straight (every value is one plus the other value for 5 spots)
      self.unique_values = []
      for card in self.total_sorter:
          if card.value not in self.unique_values:
              self.unique_values.append(card.value)
          if len(self.unique_values) < 5:
            return False, 0
      counter = 0
      for i in range(len(self.unique_values) - 1):
          if self.unique_values[i] + 1 == self.unique_values[i+1]:
              counter += 1
              if counter >= 4: # 4 connections between cards, meaning 5 total cards (1-2, or 2-3 is 1 connection)
                  return True, self.unique_values[-1]
          else:
              counter = 0
      counter = 0
      return False, 0

  def four_of_a_kind(self): # checking to see if there is four of a kind of any value
    four_value = None # finding which value brings the four of a kind, if there is a four of a kind
    for value, count in self.values_total.items():
        if count >= 4:
            four_value = value
            break
    if four_value: # grab the highest value if there is a four of a kind
        cards_of_value = [card for card in self.all_cards if card.value == four_value] # puts a list of all the cards in the same value
        four_values = [card.value for card in cards_of_value] # takes the values of the cards
        self.best_five_four = sorted(four_values, reverse=True) # makes a list of those card values from lowest to greatest
    for card in self.all_cards:
      if self.values_total[card.value] == 4:
        return True, self.best_five_four[-1]
    return False, 0

  def three_of_a_kind(self): # checking to see if there is three of a kind of any value
    three_value = None # finding which value brings the three of a kind, if there is a three of a kind
    for value, count in self.values_total.items():
        if count >= 3:
            three_value = value
            break
    if three_value: # grab the highest value if there is a three of a kind
        cards_of_value = [card for card in self.all_cards if card.value == three_value] # puts a list of all the cards in the same value
        three_values = [card.value for card in cards_of_value] # takes the values of the cards
        self.best_five_three = sorted(three_values, reverse=True) # makes a list of those card values from lowest to greatest
    for card in self.all_cards:
      if self.values_total[card.value] == 3:
        return True, self.best_five_three[-1]
    return False, 0

  def two_pair(self): # checking to see if there is a two pair of any value
    two_value = None # finding which value brings the two pair if there is a two pair
    for value, count in self.values_total.items():
        if count >= 2:
            two_value = value
    if two_value: # grab the highest value if there is a two pair
        cards_of_value = [card for card in self.all_cards if card.value == two_value] # puts a list of all the cards in the same value
        two_values = [card.value for card in cards_of_value] # takes the values of the cards
        self.best_five_two = sorted(two_values, reverse=True) # makes a list of those card values from lowest to greatest
    pair_count = 0
    for count in self.values_total.values():
        if count == 2:
            pair_count += 1
    if pair_count >= 1:
        return True, pair_count, self.best_five_two[-1]
    return False, 0, 0

  def high_card(self): # checking to see the highest card in full set
    return True, self.all_cards[-1].value

  def straight_flush(self): # checking to see if there is a straight flush
    if self.flush()[0]: # Check if flush is True
      self.unique_values = []
      for card in self.total_sorter:
          if card.value not in self.unique_values:
              self.unique_values.append(card.value)
          if len(self.unique_values) < 5:
            return False, 0
      counter = 0
      for i in range(len(self.unique_values) - 1):
          if self.unique_values[i] + 1 == self.unique_values[i+1]:
              counter += 1
              if counter >= 4: # 4 connections between cards, meaning 5 total cards (1-2, or 2-3 is 1 connection)
                  return True, self.unique_values[-1]
          else:
              counter = 0
      counter = 0
    return False, 0

  def royal_flush(self):
      is_sf, high_number = self.straight_flush()
      if is_sf and high_number == 14:
          return True, 14
      return False, 0

  def full_house(self):
    three_true, three_value = self.three_of_a_kind()
    two_true, pair_count, two_value = self.two_pair()
    if three_true and two_true and pair_count >= 1: # Ensure there's at least one pair
      if three_value > two_value:
        return True, three_value
      else:
        return True, two_value
    return False, 0

  def evaluate(self): # checking to see the highest play that one could get. assigning a value to it, the higher the value, the better it is compared to the other set the other player ha
    found, value = self.royal_flush()
    if found: return (10,value) # have to fix the royal flush to make this work
    found, value = self.straight_flush()
    if found: return (9,value)
    found, value = self.four_of_a_kind()
    if found: return (8,value)
    found, value = self.full_house()
    if found: return (7,value)
    found, value = self.flush()
    if found: return (6,value)
    found, value = self.straight()
    if found: return (5,value)
    found, value = self.three_of_a_kind()
    if found: return (4,value)
    found, pairs, value = self.two_pair()
    if pairs == 2:
      return (3,value)
    elif pairs == 1: # Added 'elif' to handle single pair case explicitly
      return (2,value)
    found, value = self.high_card()
    if found: return (1,value)
    else:
      return (0,0)

class Player:
  def __init__(self,name, chips, is_folded=False):
    self.name = name
    self.hand = []
    self.chips = chips
    self.is_folded = False
  def receive_cards(self,cards):
    self.hand = cards
  def __repr__(self):
    return(f"{self.name} has {self.hand}, and {self.chips} dollars")
  def fold(self):
    self.is_folded = True
    self.hand = []
    print(f"{self.name} has folded")
  def bet(self,amount):
    self.amount = amount
    self.chips -= self.amount
    print(f"{self.name} bets {self.amount} dollars")
    return amount
  def all_in(self):
    amount = self.chips
    print(f"{self.name} is all in")
    return amount
  def check(self):
    print(f"{self.name} checks")
    return 0

def determine_winner(players, table_cards): # determines who wins and who doesn't
    current_best_score = (-1, -1) # starts off with a score of -1, so anything that's higher will win
    winners = []

    rank_names = {
        10: "Royal Flush",
        9: "Straight Flush",
        8: "Four of a Kind",
        7: "Full House",
        6: "Flush",
        5: "Straight",
        4: "Three of a Kind",
        3: "Two Pair",
        2: "Pair",
        1: "High Card"
    } # use this to have at the end to tell what they won on, like what hand

    def card_names(values): # just gives the card names for anything after 10 so I can use later to say what their high card is
      names = {14: "Ace", 13: "King", 12: "Queen", 11: "Jack"}
      return [names.get(value, str(value)) for value in values]

    for player in players:
        if player.is_folded: # checking to see if they folded, if they did it's over
          continue
        evaluate = HandEvaluator(player.hand,table_cards)
        score = evaluate.evaluate()
        hand_name = rank_names[score[0]]
        high_card_name = card_names([score[-1]])
        if score > current_best_score: # if the score is higher, then they put it into that person's score spot and the pot goes to only them
          current_best_score = score
          winners = [player]

        elif score == current_best_score: # if the scores are the same, they tie and the pot gets split between the people
          winners.append(player)
    return winners, current_best_score

In [2]:
import time

if __name__ == "__main__":
    print("TEXAS HOLD'EM POKER")
    player_name = input("Enter your name: ")

    while True:
        try:
            starting_chips = int(input("How many chips to start? "))
            break
        except ValueError:
            print("Invalid number.")

    p1 = Player(player_name, starting_chips)
    cpu = Player("Computer", starting_chips)
    while True:
        # Check for Game Over
        if p1.chips <= 0:
            print("Game Over! You are out of chips.")
            break
        if cpu.chips <= 0:
            print("You won! Computer is bankrupt.")
            break

        # Setup Round
        round_over = False
        p1.is_folded = False
        cpu.is_folded = False
        is_all_in = False

        deck = Deck(1)
        deck.shuffle()
        game_pot = 0

        print(f"\nNEW ROUND")
        print(f"{p1.name}: ${p1.chips} vs {cpu.name}: ${cpu.chips}")

        p1.receive_cards(deck.deal())
        cpu.receive_cards(deck.deal())
        print(f"Your Hand: {p1.hand}") # shows the hand that you got, and keeps the CPU's hand hidden

        stages = [("Pre-Flop", 0), ("Flop", 3), ("Turn", 1), ("River", 1)] # sets the 4 stages of betting for a Poker game

        for stage_name, num_cards in stages: # need to split up stages into two different values, because that's how it's defined above
            for i in range(num_cards):
                deck.deal_one() # deals a card per number in that specific stage (eg. deals 3 cards for the flop)

            # prints the state of the board (the cards on the board if cards are on table)
            if num_cards > 0:
                print(f"\n--- {stage_name} (Board: {deck.table_cards}) ---")
            else:
                print(f"\n--- {stage_name} ---")

            if is_all_in:
                print(f"Dealing {stage_name} cards...")
                time.sleep(1.5) # Small delay for dramatic effect
                continue

            # betting loop
            stage_done = False # this is the fold variable to make sure someone didn't fold
            while not stage_done: # while the fold hasn't been called, run all the betting processes
                prompt = f"Bet amount (1-{p1.chips}), 'check', or 'fold': "
                bet_input = input(prompt).strip().lower()
                if bet_input in ["fold", "i fold"]: # if they have folded
                    p1.fold()
                    print(f"{p1.name} folded!")
                    cpu.chips += game_pot
                    print(f"Computer wins ${game_pot}")
                    round_over = True # resets the table, cards, and everything else
                    stage_done = True # moves on to the next section
                elif bet_input in ["check", "i check"]: # if they checked
                    p1.check()
                    print("Computer checks.")
                    stage_done = True # moves on to the next section
                else: # the actual betting portion
                    try:
                        bet_amount = int(bet_input) # makes the betting amount into a number
                        if bet_amount >= p1.chips:
                            print(f"You don't have enough chips. Going ALL-IN with ${p1.chips}!")
                            bet_amount = p1.chips
                        if bet_amount > 0: # if you bet, put the bet in a pot
                            game_pot += p1.bet(bet_amount)
                            print(f"You bet ${bet_amount}. Pot: ${game_pot}")
                            if cpu.chips > bet_amount: # if the CPU has that money, they bet as well
                                game_pot += cpu.bet(bet_amount)
                                print(f"Computer calls ${bet_amount}. Pot: ${game_pot}")
                            else:
                                amt = cpu.bet(cpu.chips) # if they don't have that amount of money, the CPU goes all in
                                game_pot += amt
                                print(f"Computer All-In ${amt}. Pot: ${game_pot}")

                            if p1.chips == 0 or cpu.chips == 0: # this is the actual ALL-IN place in the code
                                is_all_in = True
                                print("--> ALL-IN DECLARED! No more betting this round.")

                            stage_done = True # moves on to the next section
                        else:
                            print(f"Invalid amount. You have ${p1.chips}")
                    except ValueError:
                        print("Please enter a number, 'check', or 'fold'.")

            # If player folded, break the stage loop so no more cards are dealt
            if round_over:
                break

        # --- CRITICAL RESET CHECK ---
        # If round_over is True, skip to the next round resets the board completely
        if round_over:
            input("Press Enter to start next round...")
            continue

        # --- SHOWDOWN ---
        input("\nPress Enter to see winner...")
        winners, score = determine_winner([p1, cpu], deck.table_cards)

        # Payout
        split = game_pot // len(winners)
        for w in winners:
            w.chips += split

        # Print Result
        rank_names = {10: "Royal Flush", 9: "Straight Flush", 8: "Four of a Kind", 7: "Full House", 6: "Flush", 5: "Straight", 4: "Three of a Kind", 3: "Two Pair", 2: "Pair", 1: "High Card"}
        hand_name = rank_names[score[0]]

        if len(winners) == 1:
            print(f"Winner: {winners[0].name} with {hand_name}")
        else:
            print(f"Tie Game! Split pot with {hand_name}")

        # Ask to continue
        if input("\nPlay again? (y/n): ").lower() != 'y':
            break

TEXAS HOLD'EM POKER
Enter your name: Justin
How many chips to start? 10000

NEW ROUND
Justin: $10000 vs Computer: $10000
Your Hand: [Six of Diamonds, Queen of Clubs]

--- Pre-Flop ---
Bet amount (1-10000), 'check', or 'fold': check
Justin checks
Computer checks.

--- Flop (Board: [Ace of Hearts, Six of Spades, Two of Diamonds]) ---
Bet amount (1-10000), 'check', or 'fold': 100
Justin bets 100 dollars
You bet $100. Pot: $100
Computer bets 100 dollars
Computer calls $100. Pot: $200

--- Turn (Board: [Ace of Hearts, Six of Spades, Two of Diamonds, Ten of Hearts]) ---
Bet amount (1-9900), 'check', or 'fold': check
Justin checks
Computer checks.

--- River (Board: [Ace of Hearts, Six of Spades, Two of Diamonds, Ten of Hearts, Four of Clubs]) ---
Bet amount (1-9900), 'check', or 'fold': fold
Justin has folded
Justin folded!
Computer wins $200
Press Enter to start next round...

NEW ROUND
Justin: $9900 vs Computer: $10100
Your Hand: [Jack of Diamonds, Five of Clubs]

--- Pre-Flop ---
Bet amou